In [1]:
import json
import requests
import arrow

In [2]:
CC1 = 'DE'
CC2 = 'FI'
start_ts = arrow.get("2024-11-18T00:00:00Z").timestamp
end_ts   = arrow.get("2024-11-18T06:00:00Z").timestamp

"""
CC1 = 'SE'
CC2 = 'LT'
start_ts = arrow.get("2024-11-17T00:00:00Z").timestamp
end_ts   = arrow.get("2024-11-17T12:00:00Z").timestamp
"""

'\nCC1 = \'SE\'\nCC2 = \'LT\'\nstart_ts = arrow.get("2024-11-17T00:00:00Z").timestamp\nend_ts   = arrow.get("2024-11-17T12:00:00Z").timestamp\n'

In [4]:
def get_anchor_msm_meta():
    data = []
    next_url = "https://atlas.ripe.net/api/v2/anchor-measurements/"
    while next_url:
        r = requests.get( next_url )
        j = r.json()
        data.extend( j['results'] )
        next_url = j['next']
        ## print( next_url )
    return data

def get_anchor_meta():
    data = []
    next_url = "https://atlas.ripe.net/api/v2/anchors/"
    while next_url:
        r = requests.get( next_url )
        j = r.json()
        data.extend( j['results'] )
        next_url = j['next']
        ##print( next_url )
    return data

anchor_msm_meta = get_anchor_msm_meta()
anchor_meta = get_anchor_meta()

## lists of metadata for anchor and anchor msm ... should not take so much time and data is rather messy

In [5]:
# now clean this up. My eyes bleed if I look at the schema design here
# aid = anchor ID    # atx = anchor TXT description
# pid = probe ID
# mid = measurement ID

mid2aid = {}   #maps measurement to anchor
aid2mids = {}  #maps anchor to measurement list (this is incoming towards the anchor, ie the anchor is DST )
aid2info = {}  #lookup metadata based on the anchor ID
mid2info = {}  #lookup metadata based on the msms ID


for msm in anchor_msm_meta:
    if msm['is_mesh'] and msm['type'] == 'ping':
                #print( msm )
                mid = int( msm['measurement'].split('/')[-2] )
                aid = int( msm['target'].split('/')[-2] )
                
                mid2info[ mid ] = msm

                mid2aid[ mid ] = aid
                aid2mids.setdefault( aid, [] )
                aid2mids[ aid ].append( mid )

for anch in anchor_meta:
    aid2info[ aid ] = anch

In [6]:
CC1_anchors = list( filter(lambda x: x['country'] == CC1, anchor_meta ) )
CC2_anchors = list( filter(lambda x: x['country'] == CC2, anchor_meta ) )

In [7]:
# now get all the MIDs towards FI anchors / DE anchors
msm_dst_CC1 = []
for anch in CC1_anchors:
    anchor_id = anch['id']
    if anchor_id in aid2mids:
        msm_dst_CC1.extend( aid2mids[ anchor_id ] )

msm_dst_CC2 = []
for anch in CC2_anchors:
    anchor_id = anch['id']
    if anchor_id in aid2mids:
        msm_dst_CC2.extend( aid2mids[ anchor_id ] )


    

In [8]:
# now get all the prb_ids as sources
prb_src_CC1 = []
prb_src_CC2 = []

for anc in CC1_anchors:
    prb_id = anc['probe'] #GGGGGGRRRRRRRR
    prb_src_CC1.append( prb_id )

for anc in CC2_anchors:
    prb_id = anc['probe']
    prb_src_CC1.append( prb_id )


In [9]:
start_ts, end_ts

(1731888000, 1731909600)

In [17]:
from functools import lru_cache

@lru_cache(maxsize=None)
def atlasurl2json( url ):
    r = requests.get( url )
    return r.json()
    
def get_data( msm_id, start, stop, probes ):
     prb_str = ','.join(map(str, probes)) 
     url = f"https://atlas.ripe.net/api/v2/measurements/{msm_id}/results/?start={start}&stop={stop}&probe_ids={prb_str}&format=json"
     print( url )
     return atlasurl2json( url )


In [11]:
import datetime
def atlas_ping_to_timeseries( d ):
    out = {} # keyed by prb_id
    for evt in d:
        for result in evt['result']:
            if 'rtt' in result:
                out.setdefault( evt['prb_id'], {'ts': [], 'rtt': []} )
                out[ evt['prb_id'] ]['ts'].append( datetime.datetime.utcfromtimestamp( evt['timestamp'] ) )
                out[ evt['prb_id'] ]['rtt'].append( result['rtt'] )
    return out

In [12]:
#import pickle
#for msm in ( msm_dst_de ):
#    data = get_data( msm, start_ts, end_ts, prb_src_fi )
#    with open("./rawdata/{msm}.{start_ts}.{end_ts}.pcl",'wb') as outf:
#        pickle.dump( data, outf )
#        print(f"done with {msm}")

In [18]:
from matplotlib import pyplot as plt 
import seaborn as sns
import datetime
import pandas as pd

import matplotlib.dates as mdates
myFmt = mdates.DateFormatter('%H:%M')


def plot_latency_shift( data, msm, plot_title_txt ):
    out = atlas_ping_to_timeseries( data )   
    plt.close()
    plt.title( plot_title_txt )
    #plt.suptitle("RTT increase relative to the minimum observed")
    plt.ylabel("RTT increase relative to minimum observed (ms)")
    plt.xlabel("Time (UTC)")
    axs = plt.gca()
    axs.xaxis.set_major_formatter(myFmt)
    plt.grid()
    plt.ylim([0,50])
    for prb_id in out.keys():
      tseries = out[ prb_id ]['ts']
      rtts =    out[ prb_id ]['rtt']
      min_rtt = min( rtts )
      #print( min_rtt )
      rtts_norm = list( map(lambda x: x-min_rtt, rtts) )
        
      plt.plot( tseries, rtts_norm, label=prb_id, alpha=0.5 ) 
    plt.show()
    plt.savefig( f"./plots/{msm}.png" )


def atlas_ping_to_loss( d ):
    out = []
    for evt in d:
        for result in evt['result']:
            loss = 'no'
            if evt['rcvd'] < evt['sent']:
                loss = 'yes'
            out.append({
                'loss': loss,
                'prb_id': str( evt['prb_id'] ),
                'ts': datetime.datetime.utcfromtimestamp( evt['timestamp'] )    
            })
    return out

def plot_loss( data, msm, plot_title_txt ):
    loss = atlas_ping_to_loss( data )
    loss_df = pd.DataFrame.from_records( loss )
    print( loss_df.head() )
    
    sns_plot = sns.stripplot(data=loss_df, x="ts", y="prb_id", hue="loss", dodge=True, jitter=False)
    sns_plot.xaxis.set_major_formatter(myFmt)

    fig = sns_plot.get_figure()
    fig.savefig(f"./plots/sns.loss.{msm}.png")
    #sns.plt.show()


for msm in ( msm_dst_CC1 ):
    print( msm )
    data = get_data( msm, start_ts, end_ts, prb_src_CC2 )
    plot_latency_shift( data, msm, f"Anchor mesh pings ({CC2}-{CC1}) (msm_id {msm}" )
    plot_loss( data, msm, f"Anchor mesh pings ({CC2}-{CC1}) (msm_id {msm}" )

31579852
https://atlas.ripe.net/api/v2/measurements/31579852/results/?start=1731888000&stop=1731909600&probe_ids=&format=json


TypeError: string indices must be integers, not 'str'